## Performance Test - EDF Subsets
### Table of Contents
This notebook is to be used for comparing how the Trajectory Subsetter performance compares when it is executed in EDF_DEV07 versus through Harmony. This is to be compared side-by-side with it's sister notebook, performance_harmony.ipynb.

The tests were designed to be comparable subsets (similar type, size, and subset ranges) to the countering Harmony tests. These requirements led to the following test elements:

- Collection: ATL08 v005
- Granule: ATL08_20181014201628_02470113_005_01.h5
- Provider: EDF_DEV07

#### Tests:

1. ATL08 Variable Subset
2. ATL08 Bounding Box Spatial Subset
3. ATL08 Polygon Spatial Subset
4. ATL08 Temporal Subset

### Import Requirements

utilities.py pulled from [EDF tests](https://git.earthdata.nasa.gov/projects/SDPS/repos/sdps-egi-test/browse/utilities.py) on 6/8/2023.

In [ ]:
from os.path import abspath, dirname

from utilities_edf import (download_request_results, get_request_session_info,
                       get_request_session_status,
                       get_request_session_status_for_shapefile, verify_bbox_subset)

### Setup Connection Session

`utilities.py::get_request_session_info()` will retrieve the session_info object. Function will:
- Get the mode and email from the user, set the environment (uat or sit depending on the mode) and then set the server name depending on the mode (RHEL8 or RHEL7)
- Set up the Earthdata Login URL and get username/password from `.netrc` file
- Request a Bearer token from EDL
- If already have a bearer token, use it in a bogus search to see if it may be expired
- If its expired, we will revoke the token and just print a message for now and you will have to rerun this cell
- The returned `requests.Session` object will include the EDL bearer token as a headers for all requests. Further headers can optionally be included for individual requests.

In [ ]:
session_info = get_request_session_info()

### Set default parameters

In [ ]:
short_name = 'ATL08'
version = '005'
granule = 'ATL08_20181014201628_02470113_005_01.h5'
subagent_id = 'ICESAT2'
email = session_info['email_address']
client = 'ESI'
request_mode = 'async'
session_info['egi_url'] = f'https://{session_info["server_name"]}.edn.ecs.nasa.gov/{session_info["mode_name"]}/egi/request'
notebook_dir = dirname(abspath("Trajectory_Subsetter_Tests-Spatial_Subsetting.ipynb"))

requested_variables = ('/gt1l/land_segments/ph_ndx_beg,'
                       '/gt1l/land_segments/n_seg_ph,'
                       '/gt1l/land_segments/latitude,'
                       '/gt1l/land_segments/longitude,'
                       '/gt1l/land_segments/delta_time,'
                       '/gt1l/signal_photons/ph_h')
                       
bbox = '-70.5,-40,-70,-30'
polygon = 'argentina-cc.geojson'
time = '2018-10-14T20:19:04,2018-10-14T20:21:30'

### Test 1: ATL08 Variable Subset

In [ ]:
test_case_params = {'short_name': short_name,
                    'version': version,
                    'client': client,
                    'subagent_id': subagent_id,
                    'Coverage': requested_variables,
                    'request_mode': request_mode,
                    'email': email,
                    'readable_granule_name': granule}

order_id, request_status = get_request_session_status(test_case_params, session_info)
results_files = download_request_results(session_info, order_id, request_status,
                                         'variable_on-prem')

### Test 2: ATL08 Bounding Box Spatial Subset

In [ ]:
test_case_params = {'short_name': short_name,
                    'version': version,
                    'client': client,
                    'subagent_id': subagent_id,
                    'Coverage': requested_variables,
                    'request_mode': request_mode,
                    'bbox': bbox,
                    'email': email,
                    'readable_granule_name': granule}

order_id, request_status = get_request_session_status(test_case_params, session_info)
results_files = download_request_results(session_info, order_id, request_status,
                                         'bbox_edf-dev07')

for results_file in results_files:
    verify_bbox_subset(results_file, '/gt1l/land_segments/latitude,/gt1l/land_segments/longitude', test_case_params['bbox'])

### Test 3: ATL08 Polygon Spatial Subset

In [ ]:
test_case_params = {'short_name': short_name,
                    'version': version,
                    'client': client,
                    'subagent_id': subagent_id,
                    'Coverage': requested_variables,
                    'request_mode': request_mode,
                    'email': email,
                    'readable_granule_name': granule}

order_id, request_status = get_request_session_status_for_shapefile(
    test_case_params, session_info, notebook_dir,polygon)
results_files = download_request_results(session_info, order_id, request_status,
                                         'polygon_on-prem')

### Test 4: ATL08 Temporal Subset

In [ ]:
test_case_params = {'short_name': short_name,
                    'version': version,
                    'client': client,
                    'subagent_id': subagent_id,
                    'Coverage': requested_variables,
                    'request_mode': request_mode,
                    'time': time,
                    'email': email,
                    'readable_granule_name': granule}

order_id, request_status = get_request_session_status(test_case_params, session_info)
results_files = download_request_results(session_info, order_id, request_status,
                                         'temporal_edf-dev07')